# Netflix & Amazon

In [1]:
# IMDB Score voorspellen aan de hand van streamsite, genre, runtime, language etc!!!!!!!!!!!!!!!!!!!!!!!!!
import pandas as pd
import plotly.graph_objects as go
import plotly.express as px
import matplotlib.pyplot as plt
import streamlit as st

netflix_basis = pd.read_csv('NetflixOriginals.csv')
netflix_extra = pd.read_csv('netflix_original_movie_data.csv')
amazon_prime_basis = pd.read_csv('amazon prime movies.csv')

In [34]:
# 2 datasets samenvoegen
netflix_merge = pd.merge(netflix_basis, netflix_extra, on = 'Title')

# Kijken hoeveel NA's er zijn
netflix_merge.isna().sum()

# Kolommen selecteren
netflix_kolommen = netflix_merge[['Title', 'Genre', 'Premiere', 'Runtime', 'IMDB Score', 'Language_x', 'Country']]

# Duplicates verwijderen
netflix = netflix_kolommen.drop_duplicates()
amazon_prime = amazon_prime_basis.drop_duplicates()

netflix.head()

Title                  Genre           Premiere  Runtime  \
0  Enter the Anime            Documentary     August 5, 2019       58   
1      Dark Forces               Thriller    August 21, 2020       81   
2          The App  Science fiction/Drama  December 26, 2019       79   
3      Kaali Khuhi                Mystery   October 30, 2020       90   
4            Drive                 Action   November 1, 2019      147   

   IMDB Score        Language_x               Country  
0         2.5  English/Japanese  United States, Japan  
1         2.6           Spanish                Mexico  
2         2.6           Italian                 Italy  
3         3.4             Hindi                 India  
4         3.5             Hindi                 India

In [35]:
# Dataframe maken voor de Amazon language
new_amazon = pd.DataFrame(amazon_prime['Language'].value_counts())
new_amazon['Totaal'] = new_amazon['Language'].sum()
new_amazon['Percentage'] = new_amazon['Language']/new_amazon['Totaal']
new_amazon

# Dataframe maken voor de Netflix Language
new_netflix = pd.DataFrame(netflix['Language_x'].value_counts())
new_netflix['Totaal'] = new_netflix['Language_x'].sum()
new_netflix['Percentage'] = new_netflix['Language_x']/new_netflix['Totaal']
new_netflix

dropdown_buttons = [
    {'label': 'Amazon', 'method':'update',
    'args':[{'visible':[True, False]}, {'title':'Amazon'}]},
    {'label': 'Netflix', 'method':'update',
    'args':[{'visible':[False, True]}, {'title':'Netflix'}]},
    {'label': 'Beide', 'method':'update',
    'args':[{'visible':[True, True]}, {'title':'Beide'}]}
]

# Plotten van percentage films per taal met dropdownbox voor amazon, netflix en beide
fig = go.Figure()
fig.add_trace(go.Bar(x = new_amazon.index, y = new_amazon['Percentage'], name = 'Amazon Prime films/series'))
fig.add_trace(go.Bar(x = new_netflix.index, y = new_netflix['Percentage'], name = 'Netflix films/series'))
fig.update_layout({'updatemenus':[{'type': 'dropdown',
                                 'x':1.3, 'y':0.5,
                                 'showactive':True,
                                 'active': 0,
                                 'buttons':dropdown_buttons}]},
                  title_text = 'Aantal films/series die beschikbaar zijn via amazon of netflix, verdeeld per taal.', yaxis_tickformat="2%",
                 )
fig.update_xaxes(title_text = 'Taal')
fig.update_yaxes(title_text = 'Percentage films')
fig.show()

In [36]:
# Wij gaan kijken naar de 5 genres die het vaakt voorkomen
netflix['Genre'].value_counts()

# Selecteren naar de data waarbij het 1 van die 5 genres is
netflix_genre = netflix.loc[(netflix['Genre'] == 'Documentary') | (netflix['Genre'] == 'Drama')| (netflix['Genre'] == 'Comedy') | 
            (netflix['Genre'] == 'Thriller') | (netflix['Genre'] == 'Romantic comedy')]


In [74]:
# Plotten van de IMDB Scores per genre
my_scale = ['rgb(0, 171, 169)', 'rgb(0, 138, 0)', 'rgb(96, 169, 23)', 'rgb(164, 196, 0)', 'rgb(227, 200, 0)']
fig = px.box(data_frame = netflix_genre, x = 'Genre', y = 'IMDB Score', color = 'Genre', 
             color_discrete_sequence= my_scale, title = 'IMDB Scores per genre')

my_buttons = [{'label':'Boxplot', 'method':'update', 'args': [{'type': 'box'}]}, 
              {'label':'Violin', 'method':'update', 'args': [{'type': 'violin'}]}]

fig.update_layout({'updatemenus':[{'type': 'buttons', 'direction': 'down', 'x': 1.13, 'y': 0.5, 'showactive': True,
                                  'active': 0, 'buttons': my_buttons}]})

fig.show()

In [75]:
# Running time kolom omzetten naar tijden !!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!11
for time in amazon_prime[0:5]['Running Time']:
    pd.Timedelta(time)
    amazon_prime['Running Time'] = amazon_prime['Running Time'].replace(time, pd.Timedelta(time))

amazon_prime.head(10)

<ipython-input-75-49996e544f2c>:4: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



Movie Name Language IMDb Rating     Running Time  \
0                   John Rambo    Tamil           7  0 days 01:26:00   
1                 American Pie  English           7  0 days 01:35:00   
2                    Bombshell  English         6.8  0 days 01:48:00   
3                   Love Birds    Tamil         5.1  0 days 02:40:00   
4                        Hippi   Telugu           5  0 days 02:20:00   
5  Honey Bunny As Super Team X    Tamil        None            49min   
6                        Ayyaa    Tamil         5.7       2 h 39 min   
7                Mukhya Mantri  Bengali        None       1 h 57 min   
8            Gandhi Fer Aa Gea  Punjabi         4.9      2 h 13 mins   
9               Premada Vayasu  Kannada           6       1 h 56 min   

  Year of Release Maturity Rating  \
0            2008             18+   
1            1999             18+   
2            2019             18+   
3            1996             All   
4            2019             18+   
5            2018              7+   
6            2005             All   
7            1996              NR   
8            2020             13+   
9            1997              NR   

                                                Plot  
0  In Thailand, John Rambo joins a group of merce...  
1  You'll never look at warm apple pie the same w...  
2  The provocative real story of three smart, amb...  
3  After accidentally meeting, Mridula (Nagma) an...  
4  Hippi is about the live-in relationship betwee...  
5  Flamingo a Hitech Thief has created chaos in t...  
6  Ayyaa Is A Super Hit Tamil Action Movie, Direc...  
7  'Mukhya Mantri' is the story of a poor school ...  
8  Gandhi returns home from a ten year long sente...  
9  Premada Vayasu is a 1997 Indian Kannada film, ...

In [76]:
# Nieuwe kolom in netflix met runtime per groep 
bins= [0,51,101,151,251]
labels = ['0-50','51-100','101-150','151-250']
netflix['Runtime_group'] = pd.cut(netflix['Runtime'], bins=bins, labels=labels, right=False)

<ipython-input-76-29f3b8057b21>:4: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [77]:
# Visualisatie van runtime van de (Netflix)films tegen de IMDB scores !!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!
fig = go.Figure()
for runtime in netflix['Runtime_group']:
    df = netflix[netflix["Runtime_group"] == runtime]
    fig.add_trace(go.Box(x = df['Runtime_group'], y = df['IMDB Score'], name = runtime))
    
sliders = [{'steps':[
    {'label':'all', 'method': 'update', 'args': [{'visible': [True, True, True, True]}, {'title': 'Runtime'}]},
    {'label':'0-50 minuten', 'method': 'update', 'args': [{'visible': [True, False, False, False]}, {'title': 'Runtime van 0-50 minuten'}]},
    {'label':'51-100 minuten', 'method': 'update', 'args': [{'visible': [False, True, False, False]}, {'title': 'Runtime van 51-100 minuten'}]},
    {'label':'101-150 minuten', 'method': 'update', 'args': [{'visible': [False, False, True, False]}, {'title': 'Runtime van 101-150 minuten'}]},
    {'label':'151-250 minuten', 'method': 'update', 'args': [{'visible': [False, False, False, True]}, {'title': 'Runtime van 151-250 minuten'}]},
]}]

fig.update_xaxes(title_text = 'Runtime (minuten)')
fig.update_yaxes(title_text = 'IMDB Score')
fig.update_layout({'sliders': sliders})
fig.show()


In [90]:
# Als Slider niet werkt, dan kan ik hier dropdown doen voor scatter, bar en boxplot van runtime tegen IMDB
fig = go.Figure()

dropdown_buttons_2 = [
    {'label': 'Scatter', 'method':'update',
    'args':[{'visible':[True, False, False]}, {'title':'Scatterplot van de runtime tegen de IMDB Score'}]},
    {'label': 'Boxplot', 'method':'update',
    'args':[{'visible':[False, True, False]}, {'title':'Boxplot van de runtime tegen de IMDB Score'}]},
    {'label': 'Barplot', 'method':'update',
    'args':[{'visible':[False, False, True]}, {'title':'Barplot van de runtime tegen de IMDB Score'}]}    
]

fig.add_trace(go.Scatter(x = netflix['Runtime'], y = netflix['IMDB Score'], name = 'Sctterplot', mode = 'markers', marker = dict(color = 'rgb(0, 171, 169)')))

fig.add_trace(go.Box(x = netflix['Runtime_group'], y = netflix['IMDB Score'], name = 'Boxplot'))

fig.add_trace(go.Bar(x = netflix['Runtime_group'], y = netflix['IMDB Score'], name = 'Barplot'))


fig.update_layout({'updatemenus':[{'type': 'dropdown',
                                 'x':1.13, 'y':0.5,
                                 'showactive':True,
                                 'active': 0,
                                 'buttons':dropdown_buttons_2}]})

fig.update_xaxes(title_text = 'Runtime (minuten)')
fig.update_yaxes(title_text = 'IMDB Score')
fig.show()

In [31]:
# Scatterplot van de Netflix IMDB Scores per runtime
fig = px.scatter(data_frame = netflix, x = 'Runtime', y = 'IMDB Score', 
             color_discrete_sequence= ['rgb(0, 171, 169)'], title = 'IMDB Scores per runtime')

fig.show()

# Boxplot van de Netflix IMDB Scores per runtime groep
my_scale = ['rgb(0, 171, 169)', 'rgb(0, 138, 0)', 'rgb(96, 169, 23)', 'rgb(164, 196, 0)', 'rgb(227, 200, 0)', 'rgb(247, 241, 156)']
fig = px.box(data_frame = netflix, x = 'Runtime_group', y = 'IMDB Score', color = 'Runtime_group', 
             color_discrete_sequence= my_scale, title = 'IMDB Scores per runtime')

fig.show()

In [9]:
amazon_prime.head()

Movie Name Language IMDb Rating     Running Time Year of Release  \
0    John Rambo    Tamil           7  0 days 01:26:00            2008   
1  American Pie  English           7  0 days 01:35:00            1999   
2     Bombshell  English         6.8  0 days 01:48:00            2019   
3    Love Birds    Tamil         5.1  0 days 02:40:00            1996   
4         Hippi   Telugu           5  0 days 02:20:00            2019   

  Maturity Rating                                               Plot  
0             18+  In Thailand, John Rambo joins a group of merce...  
1             18+  You'll never look at warm apple pie the same w...  
2             18+  The provocative real story of three smart, amb...  
3             All  After accidentally meeting, Mridula (Nagma) an...  
4             18+  Hippi is about the live-in relationship betwee...

In [10]:
# OOK NOG NIEUWE KOLOMMEN MAKEN EN DIE GEBRUIKEN !!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!
# !!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!